# **aha-sleep-fe-cnn**
**sleep event** transforms - read event csv with converters
1. remove rows with NANs
2. transform timestamp -> uint32 minutes past 2017-01-01
3. transform event from text to enum (NAN, **ONSET**, SLEEP, **WAKEUP**, WAKE)
4. drop "step"
**series parquet** transforms - read series parquet with transforms
1. remove rows with NANs
2. transform timestamp -> uint32 minutes past 2017-01-01
3. transform zangle -> uint16 zangle
4. transform enmo -> uint16 enmo * 1000
**feature label** generation
<br>generate labels for series - X_train series, Y labels
```
for each series_id 
    set event onset time
    set event wakeup time
    for each series row
        if series time < event wakeup time
            series row label = SLEEP
        else if series time = event wakeup time
            series row label = WAKEUP
        else if series time > event wakeup time AND series time < event onset time
            series row label = WAKE
        else if series time = event onset time
            series row label = ONSET
```

**model** 
CNN using X_train, Y labels

 

In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/child-mind-institute-detect-sleep-states/train_series.parquet
/kaggle/input/child-mind-institute-detect-sleep-states/sample_submission.csv
/kaggle/input/child-mind-institute-detect-sleep-states/train_events.csv
/kaggle/input/child-mind-institute-detect-sleep-states/test_series.parquet


In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import time
import seaborn as sns
import pyarrow.parquet as pq

In [5]:
# column labels
SERIES_ID_COLUMN = 'series_id'
NIGHT_COLUMN = 'night'
EVENT_COLUMN = 'event'
STEP_COLUMN = 'step'
TIME_COLUMN = 'timestamp'

NAN_TIME = 0

ANGLEZ_COLUMN = 'anglez'
ENMO_COLUMN = 'enmo'

# event labels
ONSET_EVENT_LABEL = 'onset'
WAKEUP_EVENT_LABEL = 'wakeup'

# event enumeration
NAN_EVENT = 0
ONSET_EVENT = 1
SLEEP_EVENT = 2
WAKEUP_EVENT = 3
WAKE_EVENT = 4


In [49]:
import datetime

def remove_rows_with_nan(row):
  """Removes rows with NaN.

  Args:
    row: A Pandas Series object representing the current row of the CSV file.

  Returns:
    None if the row contains NaN, otherwise the row.
  """

  if row.isna().any():
    return None
  else:
    return row

def convert_to_minutes(date_string):
    """Converts a date string to minutes past 2017-01-01.

    Args:
    date_string: A string in the format YYYY-MM-DDTHH:MM:SS-TZ.

    Returns:
    An integer representing the number of minutes since 2017-01-01.
    """
    #print(f"date_string->,{date_string}")
    if len(date_string) == 0:
        return None # NAN_TIME
    
    # 2018-08-14T22:26:00-0400
    date_time = datetime.datetime.strptime(date_string, "%Y-%m-%dT%H:%M:%S-%f")
    #return (date_time - datetime.datetime(2018, 1, 1)).total_seconds() // 60
    #return np.int32((date_time - datetime.datetime(2017, 1, 1)).total_seconds() // 60)
    time_in_minutes = np.int32((date_time - datetime.datetime(2017, 1, 1)).total_seconds() // 60)
    #print(time_in_minutes)
    return time_in_minutes 


def convert_event_enumeration(event_string):
    if event_string == ONSET_EVENT_LABEL:
        return ONSET_EVENT
    elif event_string == WAKEUP_EVENT_LABEL:
        return WAKEUP_EVENT
    return EVENT_COLUMN  # skip column label line #1

In [50]:
print(convert_to_minutes('2018-08-14T22:26:00-0400'))
print(convert_event_enumeration('onset'))
print(convert_event_enumeration('wakeup'))
print(convert_event_enumeration('dunno'))

850946
1
3
event


In [51]:
#converters = {'remove_rows_with_nan': {'column_1': remove_rows_with_nan, 'column_2': remove_rows_with_nan}}

#converters = {'remove_rows_with_nan': {STEP_COLUMN: remove_rows_with_nan, TIME_COLUMN: remove_rows_with_nan}, TIME_COLUMN: convert_to_minutes, EVENT_COLUMN: convert_event_enumeration}
converters = {TIME_COLUMN: convert_to_minutes, EVENT_COLUMN: convert_event_enumeration}
# converters = {'timestamp': convert_to_minutes, 'event': convert_event_enumeration}

In [55]:
train_event = pd.read_csv('/kaggle/input/child-mind-institute-detect-sleep-states/train_events.csv', converters=converters)
print(len(train_events))
# drop NAN rows
train_event = train_event.dropna(axis=0)
print(len(train_event))
# drop night, step columns
train_event = train_event.drop(NIGHT_COLUMN, axis=1)
train_event = train_event.drop(STEP_COLUMN, axis=1)

train_event[TIME_COLUMN] = train_event[TIME_COLUMN].astype('uint32')
print(train_event.iloc[0])
print(train_event[TIME_COLUMN].dtype)

pd.set_option('display.max_rows', None)
train_event

9585
9585
series_id    038441c925bb
event                   1
timestamp          850946
Name: 0, dtype: object
uint32


series_id  event  timestamp
0      038441c925bb      1     850946
1      038441c925bb      3     851441
2      038441c925bb      1     852217
3      038441c925bb      3     852821
4      038441c925bb      1     853863
5      038441c925bb      3     854230
6      038441c925bb      1     855300
7      038441c925bb      3     855768
10     038441c925bb      1     858138
11     038441c925bb      3     858685
12     038441c925bb      1     859655
13     038441c925bb      3     860407
14     038441c925bb      1     861138
15     038441c925bb      3     861641
18     038441c925bb      1     863861
19     038441c925bb      3     864480
20     038441c925bb      1     865283
21     038441c925bb      3     865597
22     038441c925bb      1     866715
23     038441c925bb      3     867386
24     038441c925bb      1     868222
25     038441c925bb      3     868812
28     038441c925bb      1     871057
29     038441c925bb      3     871672
30     038441c925bb      1     872542
31     038441c925bb      3     873041
32     038441c925bb      1     873978
33     038441c925bb      3     874511
34     038441c925bb      1     875328
35     038441c925bb      3     875966
36     038441c925bb      1     876855
37     038441c925bb      3     877413
38     038441c925bb      1     878321
39     038441c925bb      3     878785
40     038441c925bb      1     879663
41     038441c925bb      3     880192
42     038441c925bb      1     881115
43     038441c925bb      3     881356
46     03d92c9f6f8a      1     742814
47     03d92c9f6f8a      3     743447
48     03d92c9f6f8a      1     744255
49     03d92c9f6f8a      3     744843
50     03d92c9f6f8a      1     745709
51     03d92c9f6f8a      3     746316
54     03d92c9f6f8a      1     748633
55     03d92c9f6f8a      3     749220
66     03d92c9f6f8a      1     757192
67     03d92c9f6f8a      3     757867
68     03d92c9f6f8a      1     758675
69     03d92c9f6f8a      3     759307
72     03d92c9f6f8a      1     761555
73     03d92c9f6f8a      3     762476
74     03d92c9f6f8a      1     762997
75     03d92c9f6f8a      3     763575
120    0402a003dae9      1    1032502
121    0402a003dae9      3    1032884
122    0402a003dae9      1    1033838
123    0402a003dae9      3    1034302
130    0402a003dae9      1    1039641
131    0402a003dae9      3    1039820
132    0402a003dae9      1    1041221
133    0402a003dae9      3    1041502
134    0402a003dae9      1    1042494
135    0402a003dae9      3    1042972
136    0402a003dae9      1    1043758
137    0402a003dae9      3    1044097
138    0402a003dae9      1    1045340
139    0402a003dae9      3    1045826
140    0402a003dae9      1    1046795
141    0402a003dae9      3    1047296
142    0402a003dae9      1    1048191
143    0402a003dae9      3    1048877
144    0402a003dae9      1    1049701
145    0402a003dae9      3    1050180
146    0402a003dae9      1    1051303
147    0402a003dae9      3    1051672
148    0402a003dae9      1    1052531
149    0402a003dae9      3    1052940
150    0402a003dae9      1    1054134
151    0402a003dae9      3    1054544
152    0402a003dae9      1    1055504
153    0402a003dae9      3    1056092
154    0402a003dae9      1    1057353
155    0402a003dae9      3    1057586
158    0402a003dae9      1    1059999
159    0402a003dae9      3    1060406
160    0402a003dae9      1    1061476
161    0402a003dae9      3    1061718
162    0402a003dae9      1    1063060
163    0402a003dae9      3    1063215
170    04f547b8017d      1    1004917
171    04f547b8017d      3    1005527
172    04f547b8017d      1    1006301
173    04f547b8017d      3    1006751
176    04f547b8017d      1    1009239
177    04f547b8017d      3    1009827
178    04f547b8017d      1    1010701
179    04f547b8017d      3    1011266
180    04f547b8017d      1    1012147
181    04f547b8017d      3    1012755
182    04f547b8017d      1    1013606
183    04f547b8017d      3    1014154
184    04f547b8017d      1    1015085
185    04f547b8017d      3    1015600
186    04f547b8017d 

In [43]:
train_events = pd.read_csv('/kaggle/input/child-mind-institute-detect-sleep-states/train_events.csv')
# drop NAN rows
#train_events = train_events.dropna(axis=0)
pd.set_option('display.max_rows', None)
train_events

series_id  night   event      step                 timestamp
0      038441c925bb      1   onset    4992.0  2018-08-14T22:26:00-0400
1      038441c925bb      1  wakeup   10932.0  2018-08-15T06:41:00-0400
2      038441c925bb      2   onset   20244.0  2018-08-15T19:37:00-0400
3      038441c925bb      2  wakeup   27492.0  2018-08-16T05:41:00-0400
4      038441c925bb      3   onset   39996.0  2018-08-16T23:03:00-0400
5      038441c925bb      3  wakeup   44400.0  2018-08-17T05:10:00-0400
6      038441c925bb      4   onset   57240.0  2018-08-17T23:00:00-0400
7      038441c925bb      4  wakeup   62856.0  2018-08-18T06:48:00-0400
8      038441c925bb      5   onset       NaN                       NaN
9      038441c925bb      5  wakeup       NaN                       NaN
10     038441c925bb      6   onset   91296.0  2018-08-19T22:18:00-0400
11     038441c925bb      6  wakeup   97860.0  2018-08-20T07:25:00-0400
12     038441c925bb      7   onset  109500.0  2018-08-20T23:35:00-0400
13     038441c925bb      7  wakeup  118524.0  2018-08-21T12:07:00-0400
14     038441c925bb      8   onset  127296.0  2018-08-22T00:18:00-0400
15     038441c925bb      8  wakeup  133332.0  2018-08-22T08:41:00-0400
16     038441c925bb      9   onset       NaN                       NaN
17     038441c925bb      9  wakeup       NaN                       NaN
18     038441c925bb     10   onset  159972.0  2018-08-23T21:41:00-0400
19     038441c925bb     10  wakeup  167400.0  2018-08-24T08:00:00-0400
20     038441c925bb     11   onset  177036.0  2018-08-24T21:23:00-0400
21     038441c925bb     11  wakeup  180804.0  2018-08-25T02:37:00-0400
22     038441c925bb     12   onset  194220.0  2018-08-25T21:15:00-0400
23     038441c925bb     12  wakeup  202272.0  2018-08-26T08:26:00-0400
24     038441c925bb     13   onset  212304.0  2018-08-26T22:22:00-0400
25     038441c925bb     13  wakeup  219384.0  2018-08-27T08:12:00-0400
26     038441c925bb     14   onset       NaN                       NaN
27     038441c925bb     14  wakeup       NaN                       NaN
28     038441c925bb     15   onset  246324.0  2018-08-28T21:37:00-0400
29     038441c925bb     15  wakeup  253704.0  2018-08-29T07:52:00-0400
30     038441c925bb     16   onset  264144.0  2018-08-29T22:22:00-0400
31     038441c925bb     16  wakeup  270132.0  2018-08-30T06:41:00-0400
32     038441c925bb     17   onset  281376.0  2018-08-30T22:18:00-0400
33     038441c925bb     17  wakeup  287772.0  2018-08-31T07:11:00-0400
34     038441c925bb     18   onset  297576.0  2018-08-31T20:48:00-0400
35     038441c925bb     18  wakeup  305232.0  2018-09-01T07:26:00-0400
36     038441c925bb     19   onset  315900.0  2018-09-01T22:15:00-0400
37     038441c925bb     19  wakeup  322596.0  2018-09-02T07:33:00-0400
38     038441c925bb     20   onset  333492.0  2018-09-02T22:41:00-0400
39     038441c925bb     20  wakeup  339060.0  2018-09-03T06:25:00-0400
40     038441c925bb     21   onset  349596.0  2018-09-03T21:03:00-0400
41     038441c925bb     21  wakeup  355944.0  2018-09-04T05:52:00-0400
42     038441c925bb     22   onset  367020.0  2018-09-04T21:15:00-0400
43     038441c925bb     22  wakeup  369912.0  2018-09-05T01:16:00-0400
44     038441c925bb     23   onset       NaN                       NaN
45     038441c925bb     23  wakeup       NaN                       NaN
46     03d92c9f6f8a      1   onset    5928.0  2018-05-31T20:14:00-0400
47     03d92c9f6f8a      1  wakeup   13524.0  2018-06-01T06:47:00-0400
48     03d92c9f6f8a      2   onset   23220.0  2018-06-01T20:15:00-0400
49     03d92c9f6f8a      2  wakeup   30276.0  2018-06-02T06:03:00-0400
50     03d92c9f6f8a      3   onset   40668.0  2018-06-02T20:29:00-0400
51     03d92c9f6f8a      3  wakeup   47952.0  2018-06-03T06:36:00-0400
52     03d92c9f6f8a      4   onset       NaN                       NaN
53     03d92c9f6f8a      4  wakeup       NaN                       NaN
54     03d92c9f6f8a      5   onset   75756.0  2018-06-04T21:13:00-0400
55     03d92c9f6f8a      5  wakeup